# Bitfinex Analysis BuyLowSellHigh

## Introduction

In this notebook, we will analyze the profitability of the BLOSEH strategy.

## BLOSEH

The Buy Low Sell High follows a simple principle:

1. Checkk all pairs. Find the pair(s) with the highest drop in price.
2. Buy some quantity of the pairs.
3. Hold the pair until the price goes up by X %, where X considers the desired profit + transaction fees.

In [1]:
import pandas as pd
from matplotlib import pyplot as plt
import os
from datetime import datetime as dtt, timedelta
import numpy as np
import warnings
from multiprocessing import Pool
import workers
from math import atan

warnings.filterwarnings('ignore')

## Data

We will only consider pairs connected to USD, to simplify the analysis. Similarly, To avoid missing data, we will only consider data from one year in the past.

In [2]:
files = [f for f in os.listdir('../../gatherers/bitfinex/data/') if 'USD.csv' in f]

start_date = dtt.now()
end_date = dtt.now() - timedelta(days=365)
pairs_dfs = {}

for f in files:
    if "TESTUSD" in f:
        continue
    df = pd.read_csv(f'../../gatherers/bitfinex/data/{f}', sep=";", index_col='mts')
    df = df[df.index > end_date.timestamp()*1000]
    pairs_dfs[f.replace('.csv','')] = df

# BLOSEH (buy low sell high) WITH MNS (minimum negative slope)

## MINIMUM NEGATIVE SLOPE APPROACH

The slope approach calculates the slopes of the last few candles for each symbol in order to make a decision. 

This approach is limitating because it is very hard to define a "minimum negative slope (MNS)" for which to check in order to buy. The principle behind MNS is to allow us to set a minimum threshold to select a coin to buy. If the threshold is not met, this means that its price hasn't fallen too much and is not attractive to invest in it.

###  Initialization

Data will be initialized in this block. All relevant parameters and variables and constants are defined here.

In [3]:
STEP_SIZE = 1 # hours
MIN_PROFIT = 0.05 # 0.1 = 10% price increase to sell
INITIAL_DINERO = 500
MIN_SLOPE_TO_BUY = -3 # degrees
MONTHLY_INVESTMENT = 300

analysis_start = end_date + timedelta(hours=STEP_SIZE)
analysis_end = start_date

current_batch_start = analysis_start - timedelta(hours=STEP_SIZE)
current_batch_end = analysis_start

dinero = INITIAL_DINERO

max_holdings = 30

current_holdings = pd.DataFrame(columns=['id','mts', 'pair', 'amount', 'price'])
current_holdings = current_holdings.set_index('id')
historical_transactions = pd.DataFrame(columns=['id', 'mts', 'pair', 'amount', 'price', 'type'])
historical_transactions = historical_transactions.set_index('id')

transaction_id_counter = 0

buy_more_this_iteration = False

current_month = analysis_start.month

In [4]:
while current_batch_end < analysis_end:
    # sanity check
    if current_holdings.shape[0] > max_holdings:
        print("WOOPS! More holdings than allowed")
        exit()

    # LOCAL DATA GENERATION
    local_chunks = {}
    for pair in pairs_dfs.keys():
        current_pair_df = pairs_dfs[pair]
        local_chunk = current_pair_df[(current_pair_df.index > current_batch_start.timestamp()*1000) & (current_pair_df.index < current_batch_end.timestamp()*1000)]
        if local_chunk.empty:
            continue
        local_chunk = local_chunk.sort_values(by='mts', ascending=False) # earliest first
        local_chunk['avg'] = (local_chunk['open'] + local_chunk['low'] + local_chunk['high'] + local_chunk['close']) / 4
        local_chunks[pair] = local_chunk

    # SELLING 
    sold_this_chunk = []
    for i, row in current_holdings.iterrows():
        pair = row['pair']
        try:
            local_chunk = local_chunks[pair]
        except KeyError as e: # no information about the current holding pair in this chunk
            continue
        if row['price'] * (1 + MIN_PROFIT) < local_chunk['high'].iloc[0]: # sell
            amount_to_sell = row['amount']
            sell_price = row['price'] * (1 + MIN_PROFIT) * row['amount']
            sell_price_with_fee = sell_price * (1 - 0.002)
            print(f"Sold {amount_to_sell} of {pair} for {sell_price_with_fee} on {current_batch_end}")
            print(f"Made profit of {row['amount'] * row['price'] * MIN_PROFIT}")
            sold_this_chunk.append(i)
            historical_transactions = historical_transactions.append({
                'id': i,
                'mts': current_batch_end,
                'pair': pair,
                'amount': row['amount'],
                'price': sell_price_with_fee, 
                'type': 'SELL'
            }, ignore_index=True)
            dinero += sell_price_with_fee
    current_holdings = current_holdings.drop(index=sold_this_chunk)


    # CHECK CURRENT HOLDINGS
    if current_holdings.shape[0] < max_holdings:
        buy_more_this_iteration = True

    if buy_more_this_iteration:
        # FIND LOWEST
        slopes = []
        for pair in local_chunks.keys():
            local_chunk = local_chunks[pair]
            slope = np.polyfit(local_chunk.index, local_chunk['avg'], 1)[0]
            slope = 360*atan(slope)/2*3.1415
            slopes.append((slope, pair))
        slopes = sorted(slopes, key=lambda tup: tup[0]) # sort by slopes lowest to highest
        to_buy = []
        for slope, pair in slopes[:(max_holdings - current_holdings.shape[0])]:
            print(f"SLOPE: {slope}")
            if slope < MIN_SLOPE_TO_BUY:
                to_buy.append((slope, pair))
        #to_buy = [(slope, pair) for slope, pair in slopes[:(max_holdings - current_holdings.shape[0])] if slope < MIN_SLOPE_TO_BUY]
        # ensures we never buy more than max_holdings and that only heavy downward slopes are bought
        for slope, pair in to_buy:
            local_chunk = local_chunks[pair]
            buy_price = local_chunk['avg'].iloc[0]
            dinero_to_spend = dinero / (max_holdings - current_holdings.shape[0])
            dinero -= dinero_to_spend
            amount_to_buy = (dinero_to_spend / buy_price) * (1-0.001) # maker fee
            print(f"Bought {amount_to_buy} of {pair} for {buy_price * amount_to_buy} on {current_batch_end} due to slope of {slope}")
            print("---------------------------------------")
            current_holdings = current_holdings.append({
                'id': transaction_id_counter,
                'mts': current_batch_end,
                'pair': pair,
                'amount': amount_to_buy,
                'price': buy_price, 
            }, ignore_index=True)
            historical_transactions = historical_transactions.append({
                'id': transaction_id_counter,
                'mts': current_batch_end,
                'pair': pair,
                'amount': amount_to_buy,
                'price': buy_price, 
                'type': 'BUY'
            }, ignore_index=True)
            transaction_id_counter += 1   
    else:
        pass

    # MONTHLY INVESTMENT
    if current_batch_start.month != current_month:
        dinero += MONTHLY_INVESTMENT
        current_month = current_batch_start.month

    current_value_of_assets = sum(current_holdings['amount'] * current_holdings['price'])
    print(f"CURRENT MONEY: {current_value_of_assets + dinero}")
    current_batch_start = current_batch_end
    current_batch_end = current_batch_end + timedelta(hours=STEP_SIZE)

print(f"FINAL DINERO: {current_value_of_assets + dinero}")
invested = (MONTHLY_INVESTMENT * 12) + INITIAL_DINERO
print(f"INVESTED: {invested}")
rend = ((current_value_of_assets + dinero) - invested) / invested
print(f"RENDIMIENTO: {rend * 100} %")
print(f"PARAMETERS USED: [{[STEP_SIZE, MIN_PROFIT, MIN_SLOPE_TO_BUY]}]")

SLOPE: -1.494722218779709
SLOPE: -0.004319562504240046
SLOPE: -0.00034650744988550447
SLOPE: -0.00022854412498528816
SLOPE: -0.00021456444998685611
SLOPE: -0.0001908461250213251
SLOPE: -0.0001633580000433508
SLOPE: -7.03695999907736e-05
SLOPE: -3.606441999914642e-05
SLOPE: -2.8901800012530167e-05
SLOPE: -2.4817850037233957e-05
SLOPE: -1.4706932253553643e-05
SLOPE: -9.517174251762508e-06
SLOPE: -5.7960674999101905e-06
SLOPE: -5.560455010320199e-06
SLOPE: -4.996555750654142e-06
SLOPE: -2.874472501396572e-06
SLOPE: -2.778656750463509e-06
SLOPE: -1.3362594640637982e-06
SLOPE: -1.3068639997425551e-06
SLOPE: -9.754357501710347e-07
SLOPE: -8.657076428054648e-07
SLOPE: -5.780360001349618e-07
SLOPE: -4.021120000329333e-07
SLOPE: -2.6859824950141556e-07
SLOPE: -2.0576825001213965e-07
SLOPE: -1.915529624827084e-07
SLOPE: -1.6351507520998106e-07
SLOPE: -1.3508449998372175e-07
SLOPE: -8.607710001137076e-08
CURRENT MONEY: 500
SLOPE: -1.9148940056035668
SLOPE: -0.0006169906000743732
SLOPE: -0.0003392

KeyboardInterrupt: 

# BLOSEH with MNPC (Minimum negative percentage change)

This approach averages the decrease in price of the latest candle to all previous candles in the current batch. It averages these changes and compares them against a threshold in order to decide whether to buy the asset or not.

For example:

c_0 (most_recent): avg price = 10
c_-1 : avg price = 15
c_-2 : avg price = 12

therefore: 

c0_c-1 : change = (10 - 15 / 15) * 100 = -33%
c0_c-2 : change = (10 - 12 / 12) * 100 = - 16%%

Average of changes  = -25% < -5% theshold, therefore we buy

## INITIALIZATION OF DATA

In [5]:
STEP_SIZE = 12 # hours
MIN_PROFIT = 0.08 # 0.1 = 10% price increase to sell
INITIAL_DINERO = 500
MIN_PCT_CHANGE_TO_BUY = -8 # pct
MONTHLY_INVESTMENT = 300

analysis_start = end_date + timedelta(hours=STEP_SIZE)
analysis_end = start_date

current_batch_start = analysis_start - timedelta(hours=STEP_SIZE)
current_batch_end = analysis_start

dinero = INITIAL_DINERO

max_holdings = 30

current_holdings = pd.DataFrame(columns=['id','mts', 'pair', 'amount', 'price'])
current_holdings = current_holdings.set_index('id')
historical_transactions = pd.DataFrame(columns=['id', 'mts', 'pair', 'amount', 'price', 'type'])
historical_transactions = historical_transactions.set_index('id')

transaction_id_counter = 0

buy_more_this_iteration = False

current_month = analysis_start.month

In [6]:
while current_batch_end < analysis_end:
    # sanity check
    if current_holdings.shape[0] > max_holdings:
        print("WOOPS! More holdings than allowed")
        exit()

    # LOCAL DATA GENERATION
    local_chunks = {}
    for pair in pairs_dfs.keys():
        current_pair_df = pairs_dfs[pair]
        local_chunk = current_pair_df[(current_pair_df.index > current_batch_start.timestamp()*1000) & (current_pair_df.index < current_batch_end.timestamp()*1000)]
        if local_chunk.empty:
            continue
        local_chunk = local_chunk.sort_values(by='mts', ascending=False) # earliest first
        local_chunk['avg'] = (local_chunk['open'] + local_chunk['low'] + local_chunk['high'] + local_chunk['close']) / 4
        local_chunks[pair] = local_chunk

    # SELLING 
    sold_this_chunk = []
    for i, row in current_holdings.iterrows():
        pair = row['pair']
        try:
            local_chunk = local_chunks[pair]
        except KeyError as e: # no information about the current holding pair in this chunk
            continue
        if row['price'] * (1 + MIN_PROFIT) < local_chunk['high'].iloc[0]: # sell
            amount_to_sell = row['amount']
            sell_price = row['price'] * (1 + MIN_PROFIT) * row['amount']
            sell_price_with_fee = sell_price * (1 - 0.002)
            print(f"Sold {amount_to_sell} of {pair} for {sell_price_with_fee} on {current_batch_end}")
            print(f"Made profit of {row['amount'] * row['price'] * MIN_PROFIT}")
            current_value_of_assets = sum(current_holdings['amount'] * current_holdings['price'])
            print(f"CURRENT MONEY: {current_value_of_assets + dinero}")
            sold_this_chunk.append(i)
            historical_transactions = historical_transactions.append({
                'id': i,
                'mts': current_batch_end,
                'pair': pair,
                'amount': row['amount'],
                'price': sell_price_with_fee, 
                'type': 'SELL'
            }, ignore_index=True)
            dinero += sell_price_with_fee
    current_holdings = current_holdings.drop(index=sold_this_chunk)


    # CHECK CURRENT HOLDINGS
    if current_holdings.shape[0] < max_holdings:
        buy_more_this_iteration = True

    if buy_more_this_iteration:
        # FIND LOWEST
        avg_changes = []
        for pair in local_chunks.keys():
            local_chunk = local_chunks[pair]
            if local_chunk.shape[0] <= 1: #prevents len(changes) = 0
                continue
            # Etc
            first_avg = local_chunk['avg'].iloc[0]
            changes = []
            for i, row in local_chunk.iloc[1:].iterrows():
                avg = row['avg']
                changes.append((first_avg - avg) / avg * 100)
            avg_changes.append((pair, sum(changes) / len(changes)))
        to_buy = [(pair, change) for pair, change in avg_changes[:(max_holdings - current_holdings.shape[0])] if change <= MIN_PCT_CHANGE_TO_BUY]
        for pair, change in to_buy:
            local_chunk = local_chunks[pair]
            buy_price = local_chunk['avg'].iloc[0]
            dinero_to_spend = dinero / (max_holdings - current_holdings.shape[0])
            dinero -= dinero_to_spend
            amount_to_buy = (dinero_to_spend / buy_price) * (1-0.001) # maker fee
            print(f"Bought {amount_to_buy} of {pair} for {buy_price * amount_to_buy} on {current_batch_end} with avg change of {change}")
            current_value_of_assets = sum(current_holdings['amount'] * current_holdings['price'])
            print(f"CURRENT MONEY: {current_value_of_assets + dinero}")
            print("---------------------------------------")
            current_holdings = current_holdings.append({
                'id': transaction_id_counter,
                'mts': current_batch_end,
                'pair': pair,
                'amount': amount_to_buy,
                'price': buy_price, 
            }, ignore_index=True)
            historical_transactions = historical_transactions.append({
                'id': transaction_id_counter,
                'mts': current_batch_end,
                'pair': pair,
                'amount': amount_to_buy,
                'price': buy_price, 
                'type': 'BUY'
            }, ignore_index=True)
            transaction_id_counter += 1   
    else:
        pass

    # MONTHLY INVESTMENT
    if current_batch_start.month != current_month:
        dinero += MONTHLY_INVESTMENT
        current_month = current_batch_start.month

    current_batch_start = current_batch_end
    current_batch_end = current_batch_end + timedelta(hours=STEP_SIZE)

print(f"FINAL DINERO: {current_value_of_assets + dinero}")
invested = (MONTHLY_INVESTMENT * 12) + INITIAL_DINERO
print(f"INVESTED: {invested}")
rend = ((current_value_of_assets + dinero) - invested) / invested
print(f"RENDIMIENTO: {rend * 100} %")
print(f"PARAMETERS USED: [{[STEP_SIZE, MIN_PROFIT, MIN_PCT_CHANGE_TO_BUY, max_holdings]}]")

Bought 118.26334014028234 of tDGBUSD for 16.650000000000002 on 2021-04-22 19:51:47.218353 with avg change of -8.81664012255043
CURRENT MONEY: 483.3333333333333
---------------------------------------
Bought 0.004785720444942657 of tMKRUSD for 16.649999999999995 on 2021-04-23 07:51:47.218353 with avg change of -13.002815392771423
CURRENT MONEY: 483.3166666666666
---------------------------------------
Bought 584.2105263157894 of tFUNUSD for 16.65 on 2021-04-23 07:51:47.218353 with avg change of -8.820956589888855
CURRENT MONEY: 483.29999999999995
---------------------------------------
Bought 1.4209515681672713 of tQTMUSD for 16.65 on 2021-04-23 07:51:47.218353 with avg change of -10.794300869404978
CURRENT MONEY: 483.28333333333325
---------------------------------------
Bought 3.733476842353099 of tXTZUSD for 16.65 on 2021-04-23 07:51:47.218353 with avg change of -8.782598392803104
CURRENT MONEY: 483.26666666666654
---------------------------------------
Bought 0.034537119624966285 of

# BLOSEH with Surfing

Surfing is described as "riding the tide until it dies down". This means that, after buying, the bot will wait until the minimum selling threshold is reached. After this, it will go into "Surfing Mode", and will not sell until the price drops by another minimum threshold. This will effectively let the bot benefit from any eventual increases in price beyond the minimum selling threshold.

In [7]:
STEP_SIZE = 12 # hours
MIN_PROFIT = 0.08 # 0.1 = 10% price increase to sell
INITIAL_DINERO = 500
MIN_PCT_CHANGE_TO_BUY = -8 # pct
MIN_PCT_DROP_TO_SELL = 0.005 # 0.005 = 0.5%
MONTHLY_INVESTMENT = 300

analysis_start = end_date + timedelta(hours=STEP_SIZE)
analysis_end = start_date

current_batch_start = analysis_start - timedelta(hours=STEP_SIZE)
current_batch_end = analysis_start

dinero = INITIAL_DINERO

max_holdings = 30

current_holdings = pd.DataFrame(columns=['id','mts', 'pair', 'amount', 'price'])
current_holdings = current_holdings.set_index('id')
historical_transactions = pd.DataFrame(columns=['id', 'mts', 'pair', 'amount', 'price', 'type'])
historical_transactions = historical_transactions.set_index('id')

transaction_id_counter = 0

buy_more_this_iteration = False

current_month = analysis_start.month

In [8]:
while current_batch_end < analysis_end:
    # sanity check
    if current_holdings.shape[0] > max_holdings:
        print("WOOPS! More holdings than allowed")
        exit()

    # LOCAL DATA GENERATION
    local_chunks = {}
    for pair in pairs_dfs.keys():
        current_pair_df = pairs_dfs[pair]
        local_chunk = current_pair_df[(current_pair_df.index > current_batch_start.timestamp()*1000) & (current_pair_df.index < current_batch_end.timestamp()*1000)]
        if local_chunk.empty:
            continue
        local_chunk = local_chunk.sort_values(by='mts', ascending=False) # earliest first
        local_chunk['avg'] = (local_chunk['open'] + local_chunk['low'] + local_chunk['high'] + local_chunk['close']) / 4
        local_chunks[pair] = local_chunk

    # SELLING 
    sold_this_chunk = []
    for i, row in current_holdings.iterrows():
        pair = row['pair']
        try:
            local_chunk = local_chunks[pair]
        except KeyError as e: # no information about the current holding pair in this chunk
            continue
        if row['price'] * (1 + MIN_PROFIT) < local_chunk['high'].iloc[0]: # sell
            ##### Analyze if the price has dropped or increased in the last chunk
            amount_to_sell = row['amount']
            sell_price = row['price'] * (1 + MIN_PROFIT) * row['amount']
            sell_price_with_fee = sell_price * (1 - 0.002)
            print(f"Sold {amount_to_sell} of {pair} for {sell_price_with_fee} on {current_batch_end}")
            print(f"Made profit of {row['amount'] * row['price'] * MIN_PROFIT}")
            current_value_of_assets = sum(current_holdings['amount'] * current_holdings['price'])
            print(f"CURRENT MONEY: {current_value_of_assets + dinero}")
            sold_this_chunk.append(i)
            historical_transactions = historical_transactions.append({
                'id': i,
                'mts': current_batch_end,
                'pair': pair,
                'amount': row['amount'],
                'price': sell_price_with_fee, 
                'type': 'SELL'
            }, ignore_index=True)
            dinero += sell_price_with_fee
    current_holdings = current_holdings.drop(index=sold_this_chunk)


    # CHECK CURRENT HOLDINGS
    if current_holdings.shape[0] < max_holdings:
        buy_more_this_iteration = True

    if buy_more_this_iteration:
        # FIND LOWEST
        avg_changes = []
        for pair in local_chunks.keys():
            local_chunk = local_chunks[pair]
            if local_chunk.shape[0] <= 1: #prevents len(changes) = 0
                continue
            # Etc
            first_avg = local_chunk['avg'].iloc[0]
            changes = []
            for i, row in local_chunk.iloc[1:].iterrows():
                avg = row['avg']
                changes.append((first_avg - avg) / avg * 100)
            avg_changes.append((pair, sum(changes) / len(changes)))
        to_buy = [(pair, change) for pair, change in avg_changes[:(max_holdings - current_holdings.shape[0])] if change <= MIN_PCT_CHANGE_TO_BUY]
        for pair, change in to_buy:
            local_chunk = local_chunks[pair]
            buy_price = local_chunk['avg'].iloc[0]
            dinero_to_spend = dinero / (max_holdings - current_holdings.shape[0])
            dinero -= dinero_to_spend
            amount_to_buy = (dinero_to_spend / buy_price) * (1-0.001) # maker fee
            print(f"Bought {amount_to_buy} of {pair} for {buy_price * amount_to_buy} on {current_batch_end} with avg change of {change}")
            current_value_of_assets = sum(current_holdings['amount'] * current_holdings['price'])
            print(f"CURRENT MONEY: {current_value_of_assets + dinero}")
            print("---------------------------------------")
            current_holdings = current_holdings.append({
                'id': transaction_id_counter,
                'mts': current_batch_end,
                'pair': pair,
                'amount': amount_to_buy,
                'price': buy_price, 
            }, ignore_index=True)
            historical_transactions = historical_transactions.append({
                'id': transaction_id_counter,
                'mts': current_batch_end,
                'pair': pair,
                'amount': amount_to_buy,
                'price': buy_price, 
                'type': 'BUY'
            }, ignore_index=True)
            transaction_id_counter += 1   
    else:
        pass

    # MONTHLY INVESTMENT
    if current_batch_start.month != current_month:
        dinero += MONTHLY_INVESTMENT
        current_month = current_batch_start.month

    current_batch_start = current_batch_end
    current_batch_end = current_batch_end + timedelta(hours=STEP_SIZE)

print(f"FINAL DINERO: {current_value_of_assets + dinero}")
invested = (MONTHLY_INVESTMENT * 12) + INITIAL_DINERO
print(f"INVESTED: {invested}")
rend = ((current_value_of_assets + dinero) - invested) / invested
print(f"RENDIMIENTO: {rend * 100} %")
print(f"PARAMETERS USED: [{[STEP_SIZE, MIN_PROFIT, MIN_PCT_CHANGE_TO_BUY, max_holdings]}]")

Bought 118.26334014028234 of tDGBUSD for 16.650000000000002 on 2021-04-22 19:51:47.218353 with avg change of -8.81664012255043
CURRENT MONEY: 483.3333333333333
---------------------------------------
Bought 0.004785720444942657 of tMKRUSD for 16.649999999999995 on 2021-04-23 07:51:47.218353 with avg change of -13.002815392771423
CURRENT MONEY: 483.3166666666666
---------------------------------------
Bought 584.2105263157894 of tFUNUSD for 16.65 on 2021-04-23 07:51:47.218353 with avg change of -8.820956589888855
CURRENT MONEY: 483.29999999999995
---------------------------------------
Bought 1.4209515681672713 of tQTMUSD for 16.65 on 2021-04-23 07:51:47.218353 with avg change of -10.794300869404978
CURRENT MONEY: 483.28333333333325
---------------------------------------
Bought 3.733476842353099 of tXTZUSD for 16.65 on 2021-04-23 07:51:47.218353 with avg change of -8.782598392803104
CURRENT MONEY: 483.26666666666654
---------------------------------------
Bought 0.034537119624966285 of